In [1]:
import numpy as np
import scipy.signal as sig
import bokeh.plotting as bkp
import bokeh.models as bkm
bkp.output_notebook()

import os
# os.environ['ARRAY_MODULE'] = 'numpy'
os.environ['CUPY_ACCELERATORS'] = 'cutensor,cub'
from asl_bloch_sim import bloch, rf
from asl_bloch_sim import xp, asnumpy

Loading BokehJS ...

In [2]:
dt = 0.00002 # seconds
# PCASL: A typical real sequence may use 750 0.5 ms, 20º, Hann RF pulses over a 1500 ms period
# 750 pulses with these durations corresponds to a duty cycle of 0.5
duration = 2.5 # seconds
label_duration = 2 # seconds
num_reps = 2500

flip_angle = 20 # degrees
rf_duration = 0.0005 # seconds
rf_bandwidth = 500 # Hz

G_max = 0.03 # T/m
G_avg = 2e-3 # T/m
S_max = 150 # T/m/s # look up max skew rate for your scanner

off_resonance = 2000 # Hz
spectrum_lines = 200

T1 = 1.65 # seconds # https://doi.org/10.1002/mrm.25197
T2 = 0.186 # seconds # https://doi.org/10.1002/mrm.21858

In [3]:
labelling_plane_thickness = rf_bandwidth / (bloch.GAMMA_BAR * G_max) # m
labelling_plane_thickness * 1e3 # mm

0.39145776523025155

In [4]:
DeltaT = label_duration / num_reps
DeltaT * 1e6 # µs

800.0

In [5]:
1/DeltaT # Hz

1250.0

In [6]:
rf_duration / DeltaT

0.625

In [7]:
G_min = (G_avg - G_max * (rf_duration / DeltaT)) / (1 - rf_duration/DeltaT)
G_min # T/m

-0.04466666666666667

In [8]:
flowrate = 0.2 # m/s
inital_position = 0.02 # m
def trajectory(t):
    """
    Return position in meters, given time in seconds.
    """
    r = flowrate * t - inital_position
    return r

In [9]:
# bokeh plot for trajectory
t = np.arange(0, duration, dt)
p = bkp.figure(width=800, height=300, title='Blood flow', x_range=(t[0], t[-1]))
p.line(t, trajectory(t), line_width=2, legend_label='Position')
p.xaxis.axis_label = 'Time (s)'
p.yaxis.axis_label = 'Position (m)'
p.line([t[0], t[-1]], [0] * 2, line_color='red', line_width=2,
       line_dash='dashed', legend_label='Labeling plane')
p.legend.click_policy = 'hide'
p.legend.location = 'top_left'
# bkp.output_file('blood_trajectory.html')
# bkp.save(p)
bkp.show(p)


In [10]:
trajectory(0) * 100, trajectory(label_duration) * 100 # cm

(-2.0, 38.0)

In [11]:
(G_max / G_avg) / (DeltaT / rf_duration) # >> 1 for no aliased labelling planes

9.375

In [12]:
time = np.arange(0, duration, dt) # seconds
position = trajectory(time)[:, np.newaxis] # meters
rf_time = np.arange(-rf_duration / 2, rf_duration / 2, dt)

rf_pulse = rf.sinc_pulse(flip_angle, rf_duration, rf_bandwidth, dt, phase_angle=0)
rf_period = rf.extend(rf_pulse, label_duration / num_reps, dt)
rf_label = np.tile(rf_period, num_reps)
rf_sig = rf.extend(rf_label, duration, dt)

G_period = np.append(np.full_like(rf_time, G_max), np.full(round((DeltaT - rf_duration) / dt), G_min))
G = rf.extend(np.tile(G_period, num_reps), duration, dt)[:, np.newaxis]

dfz = np.linspace(0, off_resonance, spectrum_lines) # Hz
B = bloch.construct_B_field(rf_sig, G, position, off_resonance=dfz)

In [13]:
B.shape

(125000, 200, 3)

In [14]:
B.size * B.itemsize / 1e9 # GB

0.3

In [15]:
type(B)

cupy.ndarray

In [16]:
abs(rf_sig.mean()) * 1e6 # µT

1.3056645821259307

In [17]:
(1 / (bloch.GAMMA_BAR * np.abs(rf_sig).max())) / dt # >> 1

225.00407503689092

In [18]:
T2 / dt # >> 1

9300.0

In [19]:
# plot RF with bokeh
plot = bkp.figure(width=800, height=400, title='RF pulse')
plot.line(rf_time * 1e3, rf_pulse.real * 1e6, line_width=2)
plot.line(rf_time * 1e3, rf_pulse.imag * 1e6, line_width=2, color='orange')
plot.xaxis.axis_label = 'Time (ms)'
plot.yaxis.axis_label = 'RF Amplitude (µT)'
bkp.show(plot)

In [20]:
NFFT = 2 ** 17
freq = np.fft.fftshift(np.fft.fftfreq(NFFT, dt))
# signal = np.append(rf_design.extend(rf_pulse, label_duration / num_reps, dt),
#                    rf_design.extend(rf_pulse * -1, label_duration / num_reps, dt)).real
amp = np.log10(np.abs(np.fft.fftshift(np.fft.fft(rf_sig.real, n=NFFT))) / 1e-6) * 20
# plot RF with bokeh
plot = bkp.figure(width=800, height=400, title='RF pulse')
plot.line(freq, amp, line_width=2)
plot.xaxis.axis_label = 'Frequency (Hz)'
plot.yaxis.axis_label = 'RF Amplitude (µT)'
bkp.show(plot)

/tmp/ipykernel_466847/827203820.py:5: RuntimeWarning: divide by zero encountered in log10
  amp = np.log10(np.abs(np.fft.fftshift(np.fft.fft(rf_sig.real, n=NFFT))) / 1e-6) * 20


In [ ]:
# plot RF with bokeh
plot = bkp.figure(width=800, height=400, title='RF pulses')
plot.line(time, rf_sig.real * 1e6, line_width=2, alpha=0.5)
plot.line(time, rf_sig.imag * 1e6, line_width=2, color='orange', alpha=0.5)
plot.xaxis.axis_label = 'Time (s)'
plot.yaxis.axis_label = 'RF Amplitude (µT)'
bkp.show(plot)

In [ ]:
# plot gradients with bokeh
plot = bkp.figure(width=800, height=400, title='Gradient pulses')
plot.line(time, G[..., 0], line_width=2, alpha=0.5, color='green')
plot.xaxis.axis_label = 'Time (s)'
plot.yaxis.axis_label = 'Gradient Amplitude (T/m)'
bkp.show(plot)

In [20]:
mags = bloch.sim(B, T1, T2, duration, dt)

  0%|          | 0/125000 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [ ]:
# plot magnetization with bokeh
plot = bkp.figure(width=800, height=400, title='Magnetization')
plot.line(time, mags[:, 0, 0], line_width=2, legend_label='Mx', alpha=0.5)
plot.line(time, mags[:, 0, 1], line_width=2, legend_label='My', color='orange', alpha=0.5)
plot.line(time, mags[:, 0, 2], line_width=2, legend_label='Mz', color='green')
plot.xaxis.axis_label = 'Time (s)'
plot.yaxis.axis_label = 'Magnetization (ref M0)'
plot.x_range = bkm.DataRange1d(start=0, end=duration)
plot.legend.click_policy = 'hide'

# bkp.output_file('magnetization_time_signal.html')
# bkp.save(plot)
bkp.show(plot)

In [ ]:
# plot magnetization off-resonances with bokeh
title = 'Longitudinal Magnetization with Off-Resonance Pulse'
plot = bkp.figure(width=1000, height=500, title=title)
for offres in range(0, end := mags.shape[1], end // 10):
    alpha = 1 - offres / end
    plot.line(time, mags[:, offres, 2], line_width=2, legend_label=f'{dfz[offres]:g} Hz',
              alpha=alpha, color='green')
plot.xaxis.axis_label = 'Time (s)'
plot.yaxis.axis_label = 'Magnetization (ref M0)'
plot.x_range = bkm.DataRange1d(start=0, end=duration)
plot.legend.click_policy = 'hide'
bkp.show(plot)

In [ ]:
# flipped = np.min(mags[..., 2], axis=0)
flipped = np.argmin(mags[..., 2], axis=0)
plot = bkp.figure(width=800, height=400, title='Flipped Magnetization Spectrum')
plot.line(dfz, np.take_along_axis(mags[..., 2], flipped[np.newaxis], axis=0)[0],
          line_width=2, legend_label='Min Mz')
plot.line(dfz, time[flipped], line_width=2, color='red', legend_label='Time of Min Mz (s)')
plot.xaxis.axis_label = 'Off-Resonance Frequency (Hz)'
plot.yaxis.axis_label = 'Magnetization (ref M0)'
plot.y_range = bkm.DataRange1d(start=-1, end=1)
plot.legend.click_policy = 'hide'
bkp.show(plot)

In [ ]:
# calculate the labelling efficiency as an average of a window after the minimum Mz
post_min_window = 0.025 # seconds # depends on T1
avg_min_long_mag = np.take_along_axis(mags[..., 2], flipped[np.newaxis] + np.arange(round(post_min_window / dt)) [:, np.newaxis], axis=0).mean(axis=0)
plot = bkp.figure(width=800, height=400, title='Average Minimum Longitudinal Magnetization Spectrum')
plot.line(dfz, avg_min_long_mag, line_width=2)
plot.xaxis.axis_label = 'Off-Resonance Frequency (Hz)'
plot.yaxis.axis_label = 'Magnetization (ref M0)'
plot.y_range = bkm.DataRange1d(start=-1, end=1)
# bkp.output_file('magnetization_spectrum.html')
# bkp.save(plot)
bkp.show(plot)

In [ ]:
avg_min_long_mag.min()

In [ ]:
# save mags, dt, and dfz to compressed numpy file
# np.savez_compressed('mags.npz', mags=mags[::10], dt=dt * 10, dfz=dfz)